In [1]:
%reload_ext autoreload
%autoreload 2


In [2]:
import os
import yaml
import urllib
from PIL import Image
from enum import Enum
from pycocotools.coco import COCO
import xml.etree.cElementTree as ET
import glob
import argparse
import numpy as np
import json
import numpy
import cv2
from collections import OrderedDict
import scipy.misc
from skimage import measure   
import random
import skimage.io as io
import matplotlib.pyplot as plt
import pylab
import shutil
import pickle
import pandas as pd
from subprocess import Popen,PIPE,STDOUT,call 
from utils import datasets

BDD100K_DIRECTORY = os.path.join('/media/dean/datastore/datasets/BerkeleyDeepDrive', 'bdd100k')
WORKING_DIRECTORY = '/media/dean/datastore/datasets/darknet'

TRAINERS_DIRECTORY = os.path.join(WORKING_DIRECTORY, 'trainers')
ANNOTATIONS_FILE = os.path.join(BDD100K_DIRECTORY, 'labels/kache_bdd100k_labels_images_train.json')

VAL_ANNOTATIONS_FILE = os.path.join(BDD100K_DIRECTORY, 'labels/bdd100k_labels_images_val.json')
COCO_ANNOTATIONS_FILE = os.path.join('/media/dean/datastore/datasets/road_coco/darknet/data/coco/annotations/instances_train2014.json')
COCO_VAL_ANNOTATIONS_FILE = os.path.join('/media/dean/datastore/datasets/road_coco/darknet/data/coco/annotations/instances_val2014.json')


BASE_DATA_CONFIG = os.path.join(WORKING_DIRECTORY, 'cfg', 'bdd100k.data')
BASE_MODEL_CONFIG = os.path.join(WORKING_DIRECTORY, 'cfg', 'yolov3-bdd100k.cfg')

In [3]:
# Prepare Dataset ##



bddfullcoco_set = datasets.DataFormatter(annotations_list = ANNOTATIONS_FILE, input_format = datasets.Format.bdd, use_cache = True,
                                 output_path = os.path.join(WORKING_DIRECTORY,'data/bddfullcoco_set'),
                                 trainer_prefix = 'COCO_train2014_0000', 
                                 s3_bucket = 'kache-scalabel/bdd100k/images/100k/train/')



Saving to Pickle File: BerkeleyDeepDrive_bdd100k_labels_kache_bdd100k_labels_images_train.json.pickle
Length of COCO Images 69863
Length of COCO Annotations: 1286871
loading annotations into memory...
Done (t=12.34s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

BIKE | Annotations: 7210  | Images:  4343
BUS | Annotations: 11672  | Images:  8993
CAR | Annotations: 713211  | Images:  69072
MOTOR | Annotations: 3002  | Images:  2284
PERSON | Annotations: 91349  | Images:  22076
RIDER | Annotations: 4517  | Images:  3586
TRAFFIC LIGHT | Annotations: 57176  | Images:  20386
TRAFFIC LIGHT-AMBER | Annotations: 3417  | Images:  2048
TRAFFIC LIGHT-GREEN | Annotations: 79406  | Images:  29193
TRAFFIC LIGHT-RED | Annotations: 46118  | Images:  18644
TRAFFIC SIGN | Annotations: 239686  | Images:  57154
TRAIN | Annotations: 136  | Images:  105
TRUCK | Annotations: 29971  | Images:  18890

################################################



In [4]:
coco_val_set = datasets.DataFormatter(annotations_list = COCO_VAL_ANNOTATIONS_FILE, input_format = datasets.Format.coco,
                                 output_path = os.path.join(WORKING_DIRECTORY,'data/coco_val_set'),use_cache = True,
                                 trainer_prefix = 'COCO_val2014_0000', 
                                 s3_bucket = 'kache-scalabel/coco_dataset/images/val2014/')


Length of COCO Images 40137
Length of COCO Annotations: 291875
loading annotations into memory...
Done (t=1.72s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

AIRPLANE | Annotations: 1445  | Images:  840
APPLE | Annotations: 1782  | Images:  491
BACKPACK | Annotations: 2891  | Images:  1832
BANANA | Annotations: 2925  | Images:  728
BASEBALL BAT | Annotations: 1022  | Images:  799
BASEBALL GLOVE | Annotations: 1206  | Images:  845
BEAR | Annotations: 462  | Images:  341
BED | Annotations: 1450  | Images:  1292
BENCH | Annotations: 3500  | Images:  1961
BIKE | Annotations: 2474  | Images:  1114
BIRD | Annotations: 3956  | Images:  1121
BOAT | Annotations: 3599  | Images:  1048
BOOK | Annotations: 8561  | Images:  1828
BOTTLE | Annotations: 8384  | Images:  2912
BOWL | Annotations: 4920  | Images:  2397
BROCCOLI | Annotations: 2697  | Images:  670
BUS | Annotations: 2027  | Images:  1350
CAKE | Annotations: 2118  | Images:  969
CAR | Annotations: 15014 

In [5]:
coco_set = datasets.DataFormatter(annotations_list = '/media/dean/datastore/datasets/darknet/data/coco_set/bdd100k/annotations/bdd100k_altered_annotations2.json', input_format = datasets.Format.bdd,
                                 output_path = os.path.join(WORKING_DIRECTORY,'data/coco_set'),use_cache = True,
                                 trainer_prefix = 'COCO_train2014_0000', 
                                 s3_bucket = 'kache-scalabel/coco_dataset/images/train2014/')


Length of COCO Images 82081
Length of COCO Annotations: 604907
loading annotations into memory...
Done (t=8.33s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

AIRPLANE | Annotations: 3833  | Images:  2243
APPLE | Annotations: 4308  | Images:  1171
BACKPACK | Annotations: 6200  | Images:  3924
BANANA | Annotations: 6912  | Images:  1618
BASEBALL BAT | Annotations: 2400  | Images:  1804
BASEBALL GLOVE | Annotations: 2689  | Images:  1884
BEAR | Annotations: 903  | Images:  668
BED | Annotations: 2905  | Images:  2539
BENCH | Annotations: 6751  | Images:  3844
BICYCLE | Annotations: 4955  | Images:  2287
BIRD | Annotations: 7290  | Images:  2241
BOAT | Annotations: 7590  | Images:  2098
BOOK | Annotations: 17315  | Images:  3734
BOTTLE | Annotations: 16983  | Images:  5968
BOWL | Annotations: 10064  | Images:  5028
BROCCOLI | Annotations: 4927  | Images:  1340
BUS | Annotations: 4327  | Images:  2791
CAKE | Annotations: 4551  | Images:  2080
CAR | Annota

In [6]:
bddfullcoco_set.merge(coco_set, include=['CONSTRUCT-BARREL','dog', 'cell phone', 'CONSTRUCT-CONE','CONSTRUCT-EQUIPMENT', 'CONSTRUCT-POLE', 'CONSTRUCT-POST', 'CONSTRUCT-SIGN', 'person', 'train', 'truck', 'car', 'traffic light', 'traffic light-red','traffic light-amber','traffic light-green', 'bus', 'bike', 'motor', 'traffic sign','traffic sign-slow_sign', 'rider','traffic sign-speed_sign', 'traffic sign-stop_sign'], reject_new_categories = True)

APPENDING to delete list: COCO_train2014_000000077020.jpg
APPENDING to delete list: COCO_train2014_000000044953.jpg
APPENDING to delete list: COCO_train2014_000000393844.jpg
APPENDING to delete list: COCO_train2014_000000277885.jpg
APPENDING to delete list: COCO_train2014_000000134946.jpg
APPENDING to delete list: COCO_train2014_000000383805.jpg
APPENDING to delete list: COCO_train2014_000000539173.jpg
APPENDING to delete list: COCO_train2014_000000302354.jpg
APPENDING to delete list: COCO_train2014_000000338323.jpg
APPENDING to delete list: COCO_train2014_000000391492.jpg
APPENDING to delete list: COCO_train2014_000000406725.jpg
APPENDING to delete list: COCO_train2014_000000545611.jpg
APPENDING to delete list: COCO_train2014_000000269749.jpg
APPENDING to delete list: COCO_train2014_000000321324.jpg
APPENDING to delete list: COCO_train2014_000000293980.jpg
APPENDING to delete list: COCO_train2014_000000421991.jpg
APPENDING to delete list: COCO_train2014_000000573572.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000371548.jpg
APPENDING to delete list: COCO_train2014_000000445845.jpg
APPENDING to delete list: COCO_train2014_000000273771.jpg
APPENDING to delete list: COCO_train2014_000000344817.jpg
APPENDING to delete list: COCO_train2014_000000040478.jpg
APPENDING to delete list: COCO_train2014_000000000595.jpg
APPENDING to delete list: COCO_train2014_000000577320.jpg
APPENDING to delete list: COCO_train2014_000000495738.jpg
APPENDING to delete list: COCO_train2014_000000259833.jpg
APPENDING to delete list: COCO_train2014_000000445887.jpg
APPENDING to delete list: COCO_train2014_000000119002.jpg
APPENDING to delete list: COCO_train2014_000000514725.jpg
APPENDING to delete list: COCO_train2014_000000278229.jpg
APPENDING to delete list: COCO_train2014_000000294838.jpg
APPENDING to delete list: COCO_train2014_000000303133.jpg
APPENDING to delete list: COCO_train2014_000000250043.jpg
APPENDING to delete list: COCO_train2014_000000442868.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000343385.jpg
APPENDING to delete list: COCO_train2014_000000456147.jpg
APPENDING to delete list: COCO_train2014_000000011222.jpg
APPENDING to delete list: COCO_train2014_000000409184.jpg
APPENDING to delete list: COCO_train2014_000000395169.jpg
APPENDING to delete list: COCO_train2014_000000335054.jpg
APPENDING to delete list: COCO_train2014_000000302655.jpg
APPENDING to delete list: COCO_train2014_000000080665.jpg
APPENDING to delete list: COCO_train2014_000000184705.jpg
APPENDING to delete list: COCO_train2014_000000532510.jpg
APPENDING to delete list: COCO_train2014_000000193738.jpg
APPENDING to delete list: COCO_train2014_000000334046.jpg
APPENDING to delete list: COCO_train2014_000000245662.jpg
APPENDING to delete list: COCO_train2014_000000324303.jpg
APPENDING to delete list: COCO_train2014_000000328582.jpg
APPENDING to delete list: COCO_train2014_000000008776.jpg
APPENDING to delete list: COCO_train2014_000000112228.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000053691.jpg
APPENDING to delete list: COCO_train2014_000000437080.jpg
APPENDING to delete list: COCO_train2014_000000056193.jpg
APPENDING to delete list: COCO_train2014_000000229550.jpg
APPENDING to delete list: COCO_train2014_000000039012.jpg
APPENDING to delete list: COCO_train2014_000000248116.jpg
APPENDING to delete list: COCO_train2014_000000554351.jpg
APPENDING to delete list: COCO_train2014_000000197305.jpg
APPENDING to delete list: COCO_train2014_000000265895.jpg
APPENDING to delete list: COCO_train2014_000000378272.jpg
APPENDING to delete list: COCO_train2014_000000437435.jpg
APPENDING to delete list: COCO_train2014_000000484369.jpg
APPENDING to delete list: COCO_train2014_000000308625.jpg
APPENDING to delete list: COCO_train2014_000000015179.jpg
APPENDING to delete list: COCO_train2014_000000472181.jpg
APPENDING to delete list: COCO_train2014_000000292868.jpg
APPENDING to delete list: COCO_train2014_000000111746.jpg
APPENDING to d

APPENDING to delete list: COCO_train2014_000000135790.jpg
APPENDING to delete list: COCO_train2014_000000176904.jpg
APPENDING to delete list: COCO_train2014_000000087205.jpg
APPENDING to delete list: COCO_train2014_000000465008.jpg
APPENDING to delete list: COCO_train2014_000000413539.jpg
APPENDING to delete list: COCO_train2014_000000553039.jpg
APPENDING to delete list: COCO_train2014_000000114219.jpg
APPENDING to delete list: COCO_train2014_000000200500.jpg
APPENDING to delete list: COCO_train2014_000000441507.jpg
APPENDING to delete list: COCO_train2014_000000397307.jpg
APPENDING to delete list: COCO_train2014_000000505122.jpg
APPENDING to delete list: COCO_train2014_000000456106.jpg
APPENDING to delete list: COCO_train2014_000000447877.jpg
APPENDING to delete list: COCO_train2014_000000047743.jpg
APPENDING to delete list: COCO_train2014_000000248958.jpg
APPENDING to delete list: COCO_train2014_000000233428.jpg
APPENDING to delete list: COCO_train2014_000000487401.jpg
APPENDING to d

...

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778 total)
PRUNING the IMAGE deletions (28778

PRUNING the ANNOTATION deletions (207403 total)
Successfully merged 53303 images | and  260378 annotations
Length of COCO Annotations: 1547249
loading annotations into memory...
Done (t=17.81s)
creating index...
index created!

########### DATASET DISTRIBUTION: ###########

BICYCLE | Annotations: 4955  | Images:  2287
BIKE | Annotations: 7210  | Images:  4343
BUS | Annotations: 15999  | Images:  11784
CAR | Annotations: 743996  | Images:  77678
CELL PHONE | Annotations: 4460  | Images:  3322
DOG | Annotations: 3774  | Images:  3041
MOTOR | Annotations: 3002  | Images:  2284
MOTORCYCLE | Annotations: 6021  | Images:  2442
PERSON | Annotations: 276665  | Images:  67250
RIDER | Annotations: 4517  | Images:  3586
STOP SIGN | Annotations: 1372  | Images:  1214
TRAFFIC LIGHT | Annotations: 66335  | Images:  23279
TRAFFIC LIGHT-AMBER | Annotations: 3417  | Images:  2048
TRAFFIC LIGHT-GREEN | Annotations: 79406  | Images:  29193
TRAFFIC LIGHT-RED | Annotations: 46118  | Images:  18644
TRAFFIC 

In [11]:
bddfullcoco_set.merge(coco_val_set, include=['CONSTRUCT-BARREL','dog', 'cell phone', 'CONSTRUCT-CONE','CONSTRUCT-EQUIPMENT', 'CONSTRUCT-POLE', 'CONSTRUCT-POST', 'CONSTRUCT-SIGN', 'person', 'train', 'truck', 'car', 'traffic light', 'traffic light-red','traffic light-amber','traffic light-green', 'bus', 'bike', 'motor', 'traffic sign','traffic sign-slow_sign', 'rider','traffic sign-speed_sign', 'traffic sign-stop_sign'], reject_new_categories = True)

EXCLUDING CATEGORIES: ['airplane', 'apple', 'backpack', 'banana', 'baseball bat', 'baseball glove', 'bear', 'bed', 'bench', 'bird', 'boat', 'book', 'bottle', 'bowl', 'broccoli', 'cake', 'carrot', 'cat', 'chair', 'clock', 'couch', 'cow', 'cup', 'dining table', 'donut', 'elephant', 'fire hydrant', 'fork', 'frisbee', 'giraffe', 'hair drier', 'handbag', 'horse', 'hot dog', 'keyboard', 'kite', 'knife', 'laptop', 'microwave', 'mouse', 'orange', 'oven', 'parking meter', 'pizza', 'potted plant', 'refrigerator', 'remote', 'sandwich', 'scissors', 'sheep', 'sink', 'skateboard', 'skis', 'snowboard', 'spoon', 'sports ball', 'suitcase', 'surfboard', 'teddy bear', 'tennis racket', 'tie', 'toaster', 'toilet', 'toothbrush', 'tv', 'umbrella', 'vase', 'wine glass', 'zebra']
PRUNING the ANNOTATION deletions (0 total)
Successfully merged 25910 images | and  124919 annotations
Length of COCO Annotations: 1672168
loading annotations into memory...
Done (t=11.15s)
creating index...
index created!

###########

In [12]:
bddfullcoco_set.export(format = datasets.Format.bdd, paginate = False)

In [14]:
annotations_file = '/media/dean/datastore/datasets/darknet/data/bddfullcoco_set/bdd100k/annotations/bdd100k_altered_annotations.json'
!cd $WORKING_DIRECTORY && python3 darkernet.py -b 'kache-scalabel/kache_ai/frames/' -a $annotations_file -f BDD -r True

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0000f77c-6257be58.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000000f77c-6257be58.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0000f77c-62c2a288.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000000f77c-62c2a288.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0000f77c-cb820c98.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000000f77c-cb820c98.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0001542f-5ce3cf52.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/00131ea7-624f538d.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_000000131ea7-624f538d.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/00134776-9123d227.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_000000134776-9123d227.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/001bad4e-2fa8f3b6.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000001bad4e-2fa8f3b6.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/001c5339-08faca55.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/002d290d-01969e7d.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000002d290d-01969e7d.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/002d290d-89d1aea8.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000002d290d-89d1aea8.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/002d290d-89f4e5c0.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000002d290d-89f4e5c0.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/002d290d-90f2bab2.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/003baca5-d6cd84e5.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000003baca5-d6cd84e5.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/003c4a61-52588960.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000003c4a61-52588960.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/003e23ee-07d32feb.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000003e23ee-07d32feb.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/003e23ee-67d25f19.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/005645a1-dbe34c9d.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_0000005645a1-dbe34c9d.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/00589f25-4cf2b9e0.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_000000589f25-4cf2b9e0.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0059f17f-f0882eef.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000059f17f-f0882eef.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/005c4fd3-cb4d6287.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

...

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0a987fbc-5adf2bca.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000a987fbc-5adf2bca.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0a987fbc-b9a867df.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000a987fbc-b9a867df.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0a987fbc-d05dedd6.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000a987fbc-d05dedd6.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0a989e4a-adbb9cd9.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0aab75aa-69cf8c75.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000aab75aa-69cf8c75.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0aab8fd1-73261fe4.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000aab8fd1-73261fe4.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0aad019b-418caa51.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000aad019b-418caa51.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0aadb8cc-b0e8cd5f.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ac0714b-952bcf85.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000ac0714b-952bcf85.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ac0714b-95c0e9b6.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000ac0714b-95c0e9b6.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ac20953-2830f7c0.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000ac20953-2830f7c0.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ac20953-3ebb3335.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ad051b9-9a51e0bf.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000ad051b9-9a51e0bf.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ad1f101-91a587d9.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000ad1f101-91a587d9.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ad47ee6-1fc7a53b.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000ad47ee6-1fc7a53b.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0ad5bdee-b3226dbc.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0af07355-56e42b91.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000af07355-56e42b91.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0af07355-d4bea79c.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000af07355-d4bea79c.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0af30faa-3a2e26aa.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1gpu_00003lr_32bat_16sd_60ep_4sb/data/coco/images/val2014/COCO_val2014_00000af30faa-3a2e26aa.jpg
SOURCE:  https://s3-us-west-2.amazonaws.com/kache-scalabel/kache_ai/frames/0af30faa-45866112.jpg
DEST:  /media/dean/datastore/datasets/darknet/trainers/20181209--cocofullandbdd_1

In [ ]:
# KACHE_S3 = 'kache-scalabel/kache_ai/frames/'
# annotations_file = os.path.join(WORKING_DIRECTORY,'data/kache_set/annotations/Kache-Logs--Tanveer-WithTrafficSigns_partial_complete_1.json')
# !cd $WORKING_DIRECTORY && python3 darkernet.py -a $annotations_file -f BDD -b $KACHE_S3 -r True

In [ ]:
# WORKING_DIR = '/media/dean/datastore1/datasets/kache_ai/frames/kache_set/'
# kache_set = datasets.DataFormatter(annotations_list = '/media/dean/datastore1/datasets/kache_ai/frames/kache_set/kacheai_logs.pickle', image_list = '/media/dean/datastore1/datasets/kache_ai/frames/kache_set/', input_format = datasets.Format.kache,
#                                  output_path = os.path.join(WORKING_DIR,'scalabel_files'), use_cache = True,
#                                  trainer_prefix = 'COCO_train2014_0000', pickle_file = '/media/dean/datastore1/datasets/Scripts/kache_ai_frames_kache_set_kacheai_logs.pickle.pickle',
#                                  s3_bucket = 'kache-scalabel/kache_ai/frames/', check_s3 = False, use_static_categories = True)


In [ ]:
# kache_set.export(format = datasets.Format.scalabel, paginate = True)

In [ ]:
# cocodd_set.merge(coco_set, include=['person', 'train', 'truck', 'car', 'traffic light', 'bus'], reject_new_categories = True)

In [ ]:
# cocodd_set.export(format = datasets.Format.bdd, paginate = False)